ACLED is using news articles as sources and creating a summary of what those sources reported in the <code>notes</code> column. Analyzing the <code>notes</code> column gives us an idea of how ACLED is using the sources. If there are distinct styles of formulating entries in this column, then this may indicate that a source is being used in a certain context. If we can identify what discrete style is being used, then the data can be tagged accordingly.

In [29]:
import pandas as pd

import spacy

# Import SpaCy English model
import en_core_web_sm

# Load English tokenizer, tagger, parser, NER and word vectors
nlp = en_core_web_sm.load()
from spacy import displacy

from collections import Counter
from pprint import pprint


base_df = pd.read_csv('../data/acled_covid19.csv')
extd_df = pd.read_csv('../data/EXPANDED_acled_covid19.csv')

Upon examining the data, it seems like most entries in the <code>notes</code> column are following a similar formula. Here we look at what the first word in each entry is, as the entries with similar formulas seem to start with the same word.

In [30]:
# It looks like the entries in the notes column all start in a similar way. Checking on that:
def _first_words(df):
    first_words = list()
    for n in df['notes']:
        s = ''
        for w in n.split(' ')[:1]:
            s += w + ' '
        first_words.append(s.strip())

    return Counter(first_words)

_first_words(base_df)

Counter({'On': 62121,
         'Security': 675,
         'Property': 121,
         'Other:': 32,
         'Around': 1757,
         'Non-violent': 80,
         'Weapons': 3,
         'Suicide': 1,
         'Change': 3,
         'Movement': 7,
         'Elections/referendum:': 1,
         'Looting:': 2,
         'Interception:': 1,
         'Recruitment:': 6,
         'Arrests:': 15,
         'Detonation:': 3,
         'Strikes:': 4,
         'Sexual': 1,
         'Agreement:': 10,
         'As': 233,
         'Between': 8,
         'Reported': 2,
         'Late': 1,
         'In': 10,
         'Assumed': 6,
         'By': 1,
         'Starting': 2})

It appears that most events are formulated where they'll say "On/Around DDMMYYYY". There are some other common words appearing which are analyzed below.

In [31]:
# Looks like most events are formulated where they'll say "On/Around DDMMYYYY". The others seem to indicate a sub_event_type.
print(
    Counter(
        base_df[base_df['notes'].str.startswith('Property')]['sub_event_type']
    )
)

Counter({'Looting/property destruction': 121})


In [32]:
print(
    Counter(
        base_df[base_df['notes'].str.startswith('Security')]['sub_event_type']
    )
)

Counter({'Change to group/activity': 673, 'Other': 2})


In [33]:
cnd1 = base_df['sub_event_type'] == 'Looting/property destruction'

_first_words(base_df[cnd1])

Counter({'Property': 121, 'Looting:': 2, 'On': 46, 'Around': 2, 'As': 1})

In [34]:
cnd1 = base_df['sub_event_type'] == 'Change to group/activity'

_first_words(base_df[cnd1])

Counter({'Security': 673,
         'Change': 3,
         'Movement': 7,
         'Recruitment:': 6,
         'On': 127,
         'Around': 13,
         'As': 35,
         'Non-violent': 1,
         'By': 1,
         'Starting': 2})

It seems like some entries in the <code>notes</code> column follow several other formulas. Some will begin their entry with some sort of categorizing word, like "security", followed by a colon and then finally discussing the contents. This structure seems to correlate with the <code>sub_event_type</code> column, but it is not an exact match.

In [35]:
all_notes = ''
for i in base_df.notes:
    all_notes += i + ' '
    
i0 = 0
i1 = 1999999
sample = all_notes[i0:i1]

In [36]:
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

stop_words = set(stopwords.words('english'))

sample_mod = sample
for s in stop_words:
    sample_mod = sample_mod.replace(s, '')

sample_mod = sample_mod.replace('  ', ' ')
print(len(sample), len(sample_mod))

1999999 1031753


In [37]:
i0 = 0
i1 = 2999999

nlp.max_length = i1-i0

sample = all_notes[i0:i1]

# Get the token-level entity annotations using the BILUO tagging scheme to describe the entity boundaries
mytext = nlp(sample)

# pprint([(X, X.ent_iob_, X.ent_type_) for X in mytext])
items = [x.text for x in mytext.ents]
Counter(items).most_common(5)

[('hundreds', 575),
 ('dozens', 476),
 ('10 January 2022', 387),
 ('around 100', 319),
 ('17 January 2022', 319)]

In [38]:
for ent in mytext.ents:
     print(ent.text, ent.start_char, ent.end_char,
           ent.label_, spacy.explain(ent.label_))

17 September 2022 3 20 DATE Absolute or relative dates or periods
Ciudad Bolivar (Bolivar 25 48 FAC Buildings, airports, highways, bridges, etc.
Venezuelan Corporation 78 100 ORG Companies, agencies, institutions, etc.
Guayana 104 111 ORG Companies, agencies, institutions, etc.
CVG 113 116 ORG Companies, agencies, institutions, etc.
16 September 2022 306 323 DATE Absolute or relative dates or periods
the All-Korean University Student Council Network 336 385 ORG Companies, agencies, institutions, etc.
Seoul Central District Court 435 463 ORG Companies, agencies, institutions, etc.
Seoul City - Seocho 465 484 GPE Countries, cities, states
15 September 2022 646 663 DATE Absolute or relative dates or periods
three 665 670 CARDINAL Numerals that do not fall under another type
the Cleaner Concern Group 690 715 ORG Companies, agencies, institutions, etc.
Hong Kong - Central 773 792 GPE Countries, cities, states
15 September 2022 894 911 DATE Absolute or relative dates or periods
Vaccine Victi

'Monday 55365 55372 DATE Absolute or relative dates or periods
Grossenhain 55403 55414 GPE Countries, cities, states
25 July 2022 55473 55485 DATE Absolute or relative dates or periods
Roberto Clemente Plaza 55527 55549 FAC Buildings, airports, highways, bridges, etc.
New York - Bronx 55553 55569 GPE Countries, cities, states
New York 55571 55579 GPE Countries, cities, states
24 July 2022 55789 55801 DATE Absolute or relative dates or periods
Les Abymes 55806 55816 PERSON People, including fictional
the University Hospital of Guadeloupe 55954 55991 ORG Companies, agencies, institutions, etc.
several months 56047 56061 DATE Absolute or relative dates or periods
24 July 2022 56176 56188 DATE Absolute or relative dates or periods
150 56190 56193 CARDINAL Numerals that do not fall under another type
No Vax 56194 56200 PRODUCT Objects, vehicles, foods, etc. (not services)
Friuli 56259 56265 GPE Countries, cities, states
23 July 2022 56416 56428 DATE Absolute or relative dates or periods
aro

dozens 107580 107586 CARDINAL Numerals that do not fall under another type
Mountain Home VA 107590 107606 ORG Companies, agencies, institutions, etc.
the Federal Workers for Freedom 107638 107669 ORG Companies, agencies, institutions, etc.
Kiwanis Park 107684 107696 LOC Non-GPE locations, mountain ranges, bodies of water
Johnson City 107700 107712 GPE Countries, cities, states
Tennessee 107714 107723 GPE Countries, cities, states
dozens 107829 107835 CARDINAL Numerals that do not fall under another type
17 June 2022 107840 107852 DATE Absolute or relative dates or periods
Ciudad Guayana 107857 107871 PERSON People, including fictional
Bolivar 107873 107880 ORG Companies, agencies, institutions, etc.
20 107883 107885 CARDINAL Numerals that do not fall under another type
SIDOR 107916 107921 ORG Companies, agencies, institutions, etc.
more than 5000 107961 107975 CARDINAL Numerals that do not fall under another type
2020 108020 108024 DATE Absolute or relative dates or periods
17 June 202

pro-Putin 168099 168108 NORP Nationalities or religious or political groups
Hamburg 168137 168144 GPE Countries, cities, states
Jungfernstieg 168152 168165 LOC Non-GPE locations, mountain ranges, bodies of water
the City Hall Market 168216 168236 FAC Buildings, airports, highways, bridges, etc.
around 700 168324 168334 CARDINAL Numerals that do not fall under another type
the District Prosecutor's Office 168456 168488 ORG Companies, agencies, institutions, etc.
Taipei City - Zhongzheng 168492 168516 GPE Countries, cities, states
Taiwan 168563 168569 GPE Countries, cities, states
the same day 168708 168720 DATE Absolute or relative dates or periods
New Party 168737 168746 ORG Companies, agencies, institutions, etc.
the Centers for Disease Control 168787 168818 ORG Companies, agencies, institutions, etc.
Taipei City - Zhongzheng 168822 168846 GPE Countries, cities, states
Taiwan 168877 168883 GPE Countries, cities, states
20 169028 169030 CARDINAL Numerals that do not fall under another 

Ciudad Guayana 223084 223098 PERSON People, including fictional
Bolivar 223100 223107 ORG Companies, agencies, institutions, etc.
the Venezuelan Corporation 223121 223147 ORG Companies, agencies, institutions, etc.
Guayana 223151 223158 ORG Companies, agencies, institutions, etc.
25 April 2022 223354 223367 DATE Absolute or relative dates or periods
Sucre 223372 223377 GPE Countries, cities, states
Chuquisaca 223379 223389 GPE Countries, cities, states
Bolivia 223573 223580 GPE Countries, cities, states
25 April 2022 223642 223655 DATE Absolute or relative dates or periods
La Paz 223660 223666 GPE Countries, cities, states
La Paz 223668 223674 PERSON People, including fictional
Bolivia 223858 223865 GPE Countries, cities, states
25 April 2022 223927 223940 DATE Absolute or relative dates or periods
Oruro 223945 223950 PERSON People, including fictional
Oruro 223952 223957 PRODUCT Objects, vehicles, foods, etc. (not services)
Bolivia 224123 224130 GPE Countries, cities, states
25 April 

...

8 November 2021 2735594 2735609 DATE Absolute or relative dates or periods
Bangladesh Jatiyatabadi Jubo Dal 2735622 2735654 ORG Companies, agencies, institutions, etc.
BNP 2735666 2735669 ORG Companies, agencies, institutions, etc.
the National Press Club 2735711 2735734 ORG Companies, agencies, institutions, etc.
Dhaka 2735738 2735743 GPE Countries, cities, states
Paltan 2735746 2735752 GPE Countries, cities, states
8 November 2021 2735859 2735874 DATE Absolute or relative dates or periods
a few hundred 2735876 2735889 CARDINAL Numerals that do not fall under another type
BJP 2735890 2735893 ORG Companies, agencies, institutions, etc.
Kolkata 2735934 2735941 GPE Countries, cities, states
a few hundred] 2736193 2736207 CARDINAL Numerals that do not fall under another type
8 November 2021 2736211 2736226 DATE Absolute or relative dates or periods
Teachers 2736239 2736247 ORG Companies, agencies, institutions, etc.
Colombo 2736313 2736320 GPE Countries, cities, states
8 November 2021 273

Pozzuoli 2796630 2796638 GPE Countries, cities, states
Napoli 2796640 2796646 GPE Countries, cities, states
Campania 2796648 2796656 GPE Countries, cities, states
4 November 2021 2796869 2796884 DATE Absolute or relative dates or periods
CSIF 2796912 2796916 ORG Companies, agencies, institutions, etc.
UGT 2796918 2796921 ORG Companies, agencies, institutions, etc.
CCOO 2796926 2796930 ORG Companies, agencies, institutions, etc.
Malaga 2796956 2796962 PERSON People, including fictional
8000 2797017 2797021 CARDINAL Numerals that do not fall under another type
4 November 2021 2797186 2797201 DATE Absolute or relative dates or periods
morning 2797224 2797231 TIME Times smaller than a day
OSS 2797260 2797263 ORG Companies, agencies, institutions, etc.
Federico Tosatto 2797382 2797398 PERSON People, including fictional
Mestre 2797409 2797415 GPE Countries, cities, states
Venezia 2797417 2797424 NORP Nationalities or religious or political groups
Veneto 2797426 2797432 GPE Countries, cities,

approximately 300 2852145 2852162 CARDINAL Numerals that do not fall under another type
Brenda Landwehr 2852201 2852216 PERSON People, including fictional
Senate 2852222 2852228 ORG Companies, agencies, institutions, etc.
Ty Masterson 2852239 2852251 PERSON People, including fictional
the International Association of Machinists and Aerospace Workers 2852272 2852337 ORG Companies, agencies, institutions, etc.
Capitol 2852364 2852371 FAC Buildings, airports, highways, bridges, etc.
Topeka 2852375 2852381 GPE Countries, cities, states
Kansas 2852383 2852389 GPE Countries, cities, states
approximately 300 2852448 2852465 CARDINAL Numerals that do not fall under another type
30 October 2021 2852470 2852485 DATE Absolute or relative dates or periods
Capitol 2852562 2852569 FAC Buildings, airports, highways, bridges, etc.
Cheyenne 2852605 2852613 GPE Countries, cities, states
30 October 2021 2852814 2852829 DATE Absolute or relative dates or periods
Unia 2852846 2852850 GPE Countries, cities,

27 October 2021 2908891 2908906 DATE Absolute or relative dates or periods
more than 10 2908908 2908920 CARDINAL Numerals that do not fall under another type
Korean 2908963 2908969 NORP Nationalities or religious or political groups
People's Council 2908984 2909000 ORG Companies, agencies, institutions, etc.
the Myeongdong Art Theater 2909063 2909089 FAC Buildings, airports, highways, bridges, etc.
Seoul City - Jung 2909104 2909121 GPE Countries, cities, states
more than 10 2909268 2909280 CARDINAL Numerals that do not fall under another type
27 October 2021 2909289 2909304 DATE Absolute or relative dates or periods
ACT 2909336 2909339 ORG Companies, agencies, institutions, etc.
Halloween 2909349 2909358 DATE Absolute or relative dates or periods
the Department of Education 2909392 2909419 ORG Companies, agencies, institutions, etc.
Pasig City 2909436 2909446 GPE Countries, cities, states
National Capital Region 2909469 2909492 ORG Companies, agencies, institutions, etc.
27 October 202

around 750 2965535 2965545 CARDINAL Numerals that do not fall under another type
Strasbourg 2965613 2965623 GPE Countries, cities, states
around 750 2965860 2965870 CARDINAL Numerals that do not fall under another type
23 October 2021 2965875 2965890 DATE Absolute or relative dates or periods
around 30 2965892 2965901 CARDINAL Numerals that do not fall under another type
Selestat 2965926 2965934 ORG Companies, agencies, institutions, etc.
around 30 2966129 2966138 CARDINAL Numerals that do not fall under another type
23 October 2021 2966143 2966158 DATE Absolute or relative dates or periods
1,600 2966176 2966181 CARDINAL Numerals that do not fall under another type
Mulhouse 2966206 2966214 GPE Countries, cities, states
1,600 2966425 2966430 CARDINAL Numerals that do not fall under another type
23 October 2021 2966435 2966450 DATE Absolute or relative dates or periods
between 50 and 100 2966452 2966470 CARDINAL Numerals that do not fall under another type
Yellow Vests 2966490 2966502 PE

In [39]:
l = [1,2,3,4,5,6,6]
l[:3]

[1, 2, 3]